## Script for generating temperature response to country-level emissions preturbation by way of FaIR
#### Mustafa Zahid, 05/27/22

In [49]:
#Importing main packages as well as packages to generate the distributions 
# from which we will pull the sets of parameters
from scipy.stats import lognorm, norm
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

### Part I: Generating climatic parameters (following Ashwin et al., 2021)

In [50]:
# Writing the functions to generate distributions for our climate parameters (inputs in FaIR model)
def lognorm_from_percentiles(x1, p1, x2, p2):
    """ Return a log-normal distribuion X parametrized by:
    
            P(X < p1) = x1
            P(X < p2) = x2
    """
    x1 = np.log(x1)
    x2 = np.log(x2)
    p1ppf = norm.ppf(p1)
    p2ppf = norm.ppf(p2)
    
    scale = (x2 - x1) / (p2ppf - p1ppf)
    mean = ((x1 * p2ppf) - (x2 * p1ppf)) / (p2ppf - p1ppf)
    
    return np.random.lognormal(mean, scale, 1000)

In [51]:
# Writing the functions to generate distributions for our climate parameters (inputs in FaIR model)
def norm_from_percentiles(x1, p1, x2, p2):
    """ Return a normal distribuion X parametrized by:
    
            P(X < p1) = x1
            P(X < p2) = x2
    """
    p1ppf = norm.ppf(p1)
    p2ppf = norm.ppf(p2)

    location = ((x1 * p2ppf) - (x2 * p1ppf)) / (p2ppf - p1ppf)
    scale = (x2 - x1) / (p2ppf - p1ppf)

    return np.random.normal(location, scale, 1000)

In [52]:
# Now iterating over the parameters to pull from the distributions
tcr = []
rwf = []
tau = []
d2 = []
ecs = []
idi = []
for i in range(1,101):
        idi.append(i)
        tcr.append(np.random.choice(lognorm_from_percentiles(1, 0.17, 2.5, 0.83)))
        rwf.append(np.random.choice(norm_from_percentiles(0.45, 0.25, 0.75, 0.75)))
        tau.append(np.random.choice(np.random.normal(4.03, 1.79, 1000)))
        d2.append(np.random.choice(lognorm_from_percentiles(1.6, 0.05, 8.4, 0.95))) 

In [53]:
# Now generate a dataframe and add the pulled parameters together
df = pd.DataFrame()
df["rwfnum"] = rwf
df["taunum"] = tau
df["tcrnum"] = tcr
df["d2num"] = d2

In [54]:
# Following Ashwin et al., we restrict our parameters 
#tau
df = df[df["taunum"] > 0] 
df = df[df["taunum"] < (2*3.95)]

#rwf
df = df[df["rwfnum"] < 1]
df = df[df["rwfnum"] > np.percentile(df["rwfnum"],6)]

#ecs
df["ecs"] = df["tcrnum"] / df["rwfnum"]

In [55]:
#generate an ID for each of the sets of parameters
df["idnum"] = range(len(df))

In [ ]:
df

### Part II: Running the FaIR model by iterating over emissions preturbation scenarios

In [1]:
# read in the needed libraries 
import numpy as np
import sys
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sn
from fair import *
#%matplotlib inline

ModuleNotFoundError: No module named 'fair'

In [113]:
# read the emissions country-year-level data
data = pd.read_csv('long_term_emissions_data_new.csv')  
data1 = pd.read_csv("country_lvl_emms_new.csv")

In [48]:
data

Year         Total
0    1750      9.350528
1    1751      9.350528
2    1752      9.354192
3    1753      9.354192
4    1754      9.357856
..    ...           ...
346  2096  80755.119641
347  2097  81247.798011
348  2098  81740.476381
349  2099  82233.154751
350  2100  82725.833121

[351 rows x 2 columns]

In [ ]:
# read the emissions country-year-level data
data = pd.read_csv('long_term_emissions_data_new_ssp2.csv')  
data1 = pd.read_csv("country_lvl_emms_new.csv")

In [ ]:
# read the emissions country-year-level data
data = pd.read_csv('long_term_emissions_data_new_ssp19.csv')  
data1 = pd.read_csv("country_lvl_emms_new.csv")

In [ ]:
data

In [ ]:
# read the emissions country-year-level data
data = pd.read_csv('long_term_emissions_data_new_ssp126.csv')  
data1 = pd.read_csv("country_lvl_emms_new.csv")

In [ ]:
data1 =  pd.DataFrame.copy(data)

In [58]:
data["Total"][data["Year"] > 2020] = 0

/var/folders/gr/k0phdc4n6vbcrm736plhstzr0000gn/T/ipykernel_9202/750264844.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data["Total"][data["Year"] > 2020] = 0


In [114]:
data = data[data["Year"] > 1979]

In [115]:
data1 = data1[data1["Year"] > 1979]

In [61]:
data

Year        Total
240  1990  22749.57436
241  1991  23238.10215
242  1992  22569.62428
243  1993  22803.49535
244  1994  22964.58336
..    ...          ...
346  2096      0.00000
347  2097      0.00000
348  2098      0.00000
349  2099      0.00000
350  2100      0.00000

[111 rows x 2 columns]

In [ ]:
data1

In [116]:
 # The following function returns an empty dataframe in the correct format for use in FaIR.
test_emissions = return_empty_emissions(df_to_copy=False, 
                                        start_year=0, 
                                        end_year=(120), 
                                        timestep=1, 
                                        scen_names=['Test'], 
                                        gases_in = ['carbon_dioxide'])

In [117]:
  # create an empty forcing dataframe compatible with test_emissions:
test_forcing = return_empty_forcing(test_emissions)

    # Note that the scenario names in the emissions and forcing dataframe must be identical for 
    #the model to run: FaIR assumes each emissions scenario corresponds directly to a single forcing scenario.
    
    # Generate a default parameter dataframe:
test_gas_parameters = get_gas_parameter_defaults()
test_thermal_parameters = get_thermal_parameter_defaults()

    # This is what the gas parameter dataframe looks like:
test_gas_parameters.head()
test_gas_parameters = test_gas_parameters.reindex(test_emissions.columns.levels[1],
                                                  axis=1,
                                                  level=1)

In [118]:
list_of_isos = pd.unique(data1["ISO3"])

In [82]:
list_of_isos

array(['AFG', 'ALB', 'DZA', 'AND', 'AGO', 'AIA', 'ATA', 'ATG', 'ARG',
       'ARM', 'ABW', 'AUS', 'AUT', 'AZE', 'BHS', 'BHR', 'BGD', 'BRB',
       'BLR', 'BEL', 'BLZ', 'BEN', 'BMU', 'BTN', 'BIH', 'BWA', 'BRA',
       'VGB', 'BRN', 'BGR', 'BFA', 'BDI', 'KHM', 'CAN', 'CPV', 'CAF',
       'TCD', 'CHL', 'CHN', 'CXR', 'COL', 'COM', 'COG', 'COK', 'CRI',
       'CIV', 'HRV', 'CUB', 'CYP', 'CZE', 'PRK', 'COD', 'DNK', 'DJI',
       'DMA', 'DOM', 'ECU', 'EGY', 'SLV', 'GNQ', 'ERI', 'EST', 'ETH',
       'FRO', 'FSM', 'FJI', 'FIN', 'FRA', 'GUF', 'PYF', 'GAB', 'GMB',
       'GEO', 'DEU', 'GHA', 'GRC', 'GRL', 'GRD', 'GLP', 'GTM', 'GIN',
       'GNB', 'GUY', 'HTI', 'HND', 'HKG', 'HUN', 'ISL', 'IND', 'IDN',
       'IRQ', 'IRL', 'IRN', 'ISR', 'ITA', 'JAM', 'JPN', 'JOR', 'KAZ',
       'KEN', 'KIR', 'KWT', 'KGZ', 'LAO', 'LVA', 'LBN', 'LSO', 'LBR',
       'LBY', 'LIE', 'LTU', 'LUX', 'MAC', 'MKD', 'MDG', 'MWI', 'MYS',
       'MDV', 'MLI', 'MLT', 'MHL', 'MTQ', 'MRT', 'MUS', 'MYT', 'MEX',
       'MNG', 'MNE',

In [119]:
master_array = np.array_split(list_of_isos, 2)

In [28]:
master_array[0]

array(['AFG', 'ALB', 'DZA', 'AND', 'AGO', 'AIA', 'ATA', 'ATG', 'ARG',
       'ARM', 'ABW', 'AUS', 'AUT', 'AZE', 'BHS', 'BHR', 'BGD', 'BRB',
       'BLR', 'BEL', 'BLZ', 'BEN', 'BMU', 'BTN', 'BIH', 'BWA', 'BRA',
       'VGB', 'BRN', 'BGR', 'BFA', 'BDI', 'KHM', 'CAN', 'CPV', 'CAF',
       'TCD', 'CHL', 'CHN', 'CXR', 'COL', 'COM', 'COG', 'COK', 'CRI',
       'CIV', 'HRV', 'CUB', 'CYP', 'CZE', 'PRK', 'COD', 'DNK', 'DJI',
       'DMA', 'DOM', 'ECU', 'EGY', 'SLV', 'GNQ', 'ERI', 'EST', 'ETH',
       'FRO', 'FSM', 'FJI', 'FIN', 'FRA', 'GUF', 'PYF', 'GAB', 'GMB',
       'GEO', 'DEU', 'GHA', 'GRC', 'GRL', 'GRD', 'GLP', 'GTM', 'GIN',
       'GNB', 'GUY', 'HTI', 'HND', 'HKG', 'HUN', 'ISL', 'IND', 'IDN',
       'IRQ', 'IRL', 'IRN', 'ISR', 'ITA', 'JAM', 'JPN', 'JOR', 'KAZ',
       'KEN', 'KIR', 'KWT', 'KGZ', 'LAO', 'LVA', 'LBN', 'LSO', 'LBR',
       'LBY'], dtype=object)

In [ ]:
i = "USA"

In [ ]:
data_iso = data1[data1["ISO3"] == i]

In [ ]:
data_iso = data_iso[["Year", "Total"]]
data_iso

In [ ]:
data_new = pd.merge(data, data_iso, on = "Year")

In [ ]:
data_new

In [ ]:
data_iso.rename(columns = {'Total':'Total_iso'}, inplace = True)

In [122]:
list_dfs = []
for m in range(1,len(df)): 
    for i in master_array[1]:
        # shut off emissions from country i
        data_iso = data1[data1["ISO3"] == i]
        data_iso = data_iso[["Year", "Total"]]
        data_iso.rename(columns = {'Total':'Total_iso'}, inplace = True)
        data_new = pd.merge(data, data_iso, on = "Year")
        data_new["Total"] = data_new["Total"] - data_new["Total_iso"]
        data_new = data_new[["Year", "Total"]]
        data_new.rename(columns = {'Total':'carbon_dioxide'}, inplace = True) #change name to match emissions data
        data_new.rename(columns = {'Year':'year'}, inplace = True) #change name to match emissions data
        data_new["year"] = pd.to_numeric(data_new["year"]) 
        # since the carbon emissions are on MtCO2, we need to convert to GtC
        data_new['carbon_dioxide'] = (data_new['carbon_dioxide'] / 1000) / 3.67 
        data_new = data_new[data_new["year"] >= 1980].reset_index() # only keep 1980 and forward
        data_new['year'] = data_new['year'] - (min(data_new['year']) - 1) 
        #feed updated emissions to test_emissions
        test_emissions[("Test", "carbon_dioxide")] = data_new['carbon_dioxide']
        # test_gas_parameters[("default", "carbon_dioxide")][6] = list(df1["taunum"])[0]
        
        # therefore use central estimates for d1-3, q1; and set q2, q3 to return "correct" TCR/ECS values
        df1 = df[df['idnum'] == m] 
        d1 = 0.903
        d2 = list(df1["d2num"])[0]
        d3 = 355
        q1 = 0.180
        rwf = list(df1["rwfnum"])[0]

        TCR = list(df1["tcrnum"])[0]
        ECS = TCR / rwf
        F_2x = 3.759

        v1 = (1-(d1/69.66) * (1-np.exp(-69.66/d1)) )
        v2 = (1-(d2/69.66) * (1-np.exp(-69.66/d2)) )
        v3 = (1-(d3/69.66) * (1-np.exp(-69.66/d3)) )

        q3 = (((TCR/F_2x) - q1*(v1-v2) - (ECS/F_2x)*v2) / (v3-v2))
        q2 = (ECS/F_2x - q1 -  q3)

        test_thermal_parameters["default",2][1] = q2
        test_thermal_parameters["default",3][1] = q3

            #test_thermal_parameters = pd.DataFrame([[d1,d2,d3],[q1,q2,q3]],
             #                                      index=['d','q'],
              #                                     columns=pd.MultiIndex.from_product([['default'],
                      #                                                                 [1,2,3]]))
        pulse_run = run_FaIR(emissions_in=test_emissions,
                             forcing_in=test_forcing,
                             gas_parameters=test_gas_parameters,
                             thermal_parameters=test_thermal_parameters)
        temp_response = pulse_run['T']
        #(temp_response.temp_response).apply(lambda x: float(x))   
            #temp_response["temp_response"] = float(temp_response["temp_response"]) 
            #temp_response.to_csv('temp_response/tempresponse' + "_" + str(k) + "_" + str(iso) + '.csv') 
        temp_response["loop"] = str(m) + "_loop_" + i   
        list_dfs.append(temp_response)

Integrating 1 scenarios, 1 gas cycle parameter sets, 1 thermal response parameter sets, over ['carbon_dioxide'] forcing agents, between 0 and 120...


100%|████████████████████████████████| 120/120 [00:00<00:00, 5517.25 timestep/s]

Integrating 1 scenarios, 1 gas cycle parameter sets, 1 thermal response parameter sets, over ['carbon_dioxide'] forcing agents, between 0 and 120...



100%|████████████████████████████████| 120/120 [00:00<00:00, 4855.17 timestep/s]

Integrating 1 scenarios, 1 gas cycle parameter sets, 1 thermal response parameter sets, over ['carbon_dioxide'] forcing agents, between 0 and 120...


...


100%|████████████████████████████████| 120/120 [00:00<00:00, 6000.94 timestep/s]

Integrating 1 scenarios, 1 gas cycle parameter sets, 1 thermal response parameter sets, over ['carbon_dioxide'] forcing agents, between 0 and 120...



100%|████████████████████████████████| 120/120 [00:00<00:00, 5726.21 timestep/s]

Integrating 1 scenarios, 1 gas cycle parameter sets, 1 thermal response parameter sets, over ['carbon_dioxide'] forcing agents, between 0 and 120...



100%|████████████████████████████████| 120/120 [00:00<00:00, 5854.22 timestep/s]


In [ ]:
list_dfs

In [123]:
pd.concat(list_dfs).to_csv("fair_temp_resp_k80_hist_fut_bilateral1.csv")

In [ ]:
data_iso = data1[data1["ISO3"] == "ALB"]

In [ ]:
data_iso = data_iso[["Year", "Total"]]

In [ ]:
data_iso

In [ ]:
data_iso.rename(columns = {'Total':'Total_iso'}, inplace = True)

In [ ]:
data_new = pd.merge(data, data_iso, on = "Year")

In [ ]:
data_new["Total"] = data_new["Total"] - data_new["Total_iso"]

In [ ]:
data_new = data_new[["Year", "Total"]]

In [ ]:
data_new.rename(columns = {'Total':'carbon_dioxide'}, inplace = True) #change name to match emissions data

In [ ]:
data_new.rename(columns = {'Year':'year'}, inplace = True) #change name to match emissions data
data_new["year"] = pd.to_numeric(data_new["year"]) 
        # since the carbon emissions are on MtCO2, we need to convert to GtC
data_new['carbon_dioxide'] = (data_new['carbon_dioxide'] / 1000) / 3.67 
data_new = data_new[data_new["year"] >= 1980].reset_index() # only keep 1980 and forward
data_new['year'] = data_new['year'] - (min(data_new['year']) - 1) 
        #feed updated emissions to test_emissions
test_emissions[("Test", "carbon_dioxide")] = data_new['carbon_dioxide']
        # test_gas_parameters[("default", "carbon_dioxide")][6] = list(df1["ta

In [124]:
list_dfs = []
for m in range(1,len(df)): 
  #  for i in master_array[9]:
        # shut off emissions from country i
#        data_iso = data1[data1["ISO3"] == i]
 #       data_iso = data_iso[["Year", "Total"]]
  #      data_iso.rename(columns = {'Total':'Total_iso'}, inplace = True)
   #     data_new = pd.merge(data, data_iso, on = "Year")
    #    data_new["Total"] = data_new["Total"] - data_new["Total_iso"]
    data_new = data
    data_new = data_new[["Year", "Total"]]
    data_new.rename(columns = {'Total':'carbon_dioxide'}, inplace = True) #change name to match emissions data
    data_new.rename(columns = {'Year':'year'}, inplace = True) #change name to match emissions data
    data_new["year"] = pd.to_numeric(data_new["year"]) 
    # since the carbon emissions are on MtCO2, we need to convert to GtC
    data_new['carbon_dioxide'] = (data_new['carbon_dioxide'] / 1000) / 3.67 
    data_new = data_new[data_new["year"] >= 1980].reset_index() # only keep 1980 and forward
    data_new['year'] = data_new['year'] - (min(data_new['year']) - 1) 
    #feed updated emissions to test_emissions
    test_emissions[("Test", "carbon_dioxide")] = data_new['carbon_dioxide']
        # test_gas_parameters[("default", "carbon_dioxide")][6] = list(df1["taunum"])[0]
        
        # therefore use central estimates for d1-3, q1; and set q2, q3 to return "correct" TCR/ECS values
    df1 = df[df['idnum'] == m] 
    d1 = 0.903
    d2 = list(df1["d2num"])[0]
    d3 = 355
    q1 = 0.180
    rwf = list(df1["rwfnum"])[0]

    TCR = list(df1["tcrnum"])[0]
    ECS = TCR / rwf
    F_2x = 3.759

    v1 = (1-(d1/69.66) * (1-np.exp(-69.66/d1)) )
    v2 = (1-(d2/69.66) * (1-np.exp(-69.66/d2)) )
    v3 = (1-(d3/69.66) * (1-np.exp(-69.66/d3)) )

    q3 = (((TCR/F_2x) - q1*(v1-v2) - (ECS/F_2x)*v2) / (v3-v2))
    q2 = (ECS/F_2x - q1 -  q3)

    test_thermal_parameters["default",2][1] = q2
    test_thermal_parameters["default",3][1] = q3

            #test_thermal_parameters = pd.DataFrame([[d1,d2,d3],[q1,q2,q3]],
             #                                      index=['d','q'],
              #                                     columns=pd.MultiIndex.from_product([['default'],
                      #                                                                 [1,2,3]]))
    pulse_run = run_FaIR(emissions_in=test_emissions,
                         forcing_in=test_forcing,
                         gas_parameters=test_gas_parameters,
                         thermal_parameters=test_thermal_parameters)
    temp_response = pulse_run['T']
        #(temp_response.temp_response).apply(lambda x: float(x))   
            #temp_response["temp_response"] = float(temp_response["temp_response"]) 
            #temp_response.to_csv('temp_response/tempresponse' + "_" + str(k) + "_" + str(iso) + '.csv') 
    temp_response["loop"] = str(m) + "_loop_all" 
    list_dfs.append(temp_response)

Integrating 1 scenarios, 1 gas cycle parameter sets, 1 thermal response parameter sets, over ['carbon_dioxide'] forcing agents, between 0 and 120...


100%|████████████████████████████████| 120/120 [00:00<00:00, 6478.44 timestep/s]

Integrating 1 scenarios, 1 gas cycle parameter sets, 1 thermal response parameter sets, over ['carbon_dioxide'] forcing agents, between 0 and 120...



100%|████████████████████████████████| 120/120 [00:00<00:00, 5554.51 timestep/s]

Integrating 1 scenarios, 1 gas cycle parameter sets, 1 thermal response parameter sets, over ['carbon_dioxide'] forcing agents, between 0 and 120...


...


100%|████████████████████████████████| 120/120 [00:00<00:00, 5314.40 timestep/s]

Integrating 1 scenarios, 1 gas cycle parameter sets, 1 thermal response parameter sets, over ['carbon_dioxide'] forcing agents, between 0 and 120...



100%|████████████████████████████████| 120/120 [00:00<00:00, 5163.28 timestep/s]

Integrating 1 scenarios, 1 gas cycle parameter sets, 1 thermal response parameter sets, over ['carbon_dioxide'] forcing agents, between 0 and 120...



100%|████████████████████████████████| 120/120 [00:00<00:00, 5804.19 timestep/s]


In [103]:
pd.concat(list_dfs).to_csv("fair_temp_resp_k80_hist_fut_bilateralfull.csv")

In [ ]:
pd.concat(list_dfs).to_csv("fair_temp_resp_k80_hist_futall_ssp245_noemms.csv")

In [ ]:
data

In [ ]:
data[data["Year"] > 2020]["Total"] = 0

In [ ]:
data["Total"][data["Year"] > 2020] = 0

In [ ]:
data

In [ ]:
list_dfs = []
for m in range(1,len(df)): 
  #  for i in master_array[9]:
        # shut off emissions from country i
#        data_iso = data1[data1["ISO3"] == i]
 #       data_iso = data_iso[["Year", "Total"]]
  #      data_iso.rename(columns = {'Total':'Total_iso'}, inplace = True)
   #     data_new = pd.merge(data, data_iso, on = "Year")
    #    data_new["Total"] = data_new["Total"] - data_new["Total_iso"]
    data_new = data
    data_new = data_new[["Year", "Total"]]
    data_new.rename(columns = {'Total':'carbon_dioxide'}, inplace = True) #change name to match emissions data
    data_new.rename(columns = {'Year':'year'}, inplace = True) #change name to match emissions data
    data_new["year"] = pd.to_numeric(data_new["year"]) 
    # since the carbon emissions are on MtCO2, we need to convert to GtC
    data_new['carbon_dioxide'] = (data_new['carbon_dioxide'] / 1000) / 3.67 
    data_new = data_new[data_new["year"] >= 1990].reset_index() # only keep 1980 and forward
    data_new['year'] = data_new['year'] - (min(data_new['year']) - 1) 
    #feed updated emissions to test_emissions
    test_emissions[("Test", "carbon_dioxide")] = data_new['carbon_dioxide']
        # test_gas_parameters[("default", "carbon_dioxide")][6] = list(df1["taunum"])[0]
        
        # therefore use central estimates for d1-3, q1; and set q2, q3 to return "correct" TCR/ECS values
    df1 = df[df['idnum'] == m] 
    d1 = 0.903
    d2 = list(df1["d2num"])[0]
    d3 = 355
    q1 = 0.180
    rwf = list(df1["rwfnum"])[0]

    TCR = list(df1["tcrnum"])[0]
    ECS = TCR / rwf
    F_2x = 3.759

    v1 = (1-(d1/69.66) * (1-np.exp(-69.66/d1)) )
    v2 = (1-(d2/69.66) * (1-np.exp(-69.66/d2)) )
    v3 = (1-(d3/69.66) * (1-np.exp(-69.66/d3)) )

    q3 = (((TCR/F_2x) - q1*(v1-v2) - (ECS/F_2x)*v2) / (v3-v2))
    q2 = (ECS/F_2x - q1 -  q3)

    test_thermal_parameters["default",2][1] = q2
    test_thermal_parameters["default",3][1] = q3

            #test_thermal_parameters = pd.DataFrame([[d1,d2,d3],[q1,q2,q3]],
             #                                      index=['d','q'],
              #                                     columns=pd.MultiIndex.from_product([['default'],
                      #                                                                 [1,2,3]]))
    pulse_run = run_FaIR(emissions_in=test_emissions,
                         forcing_in=test_forcing,
                         gas_parameters=test_gas_parameters,
                         thermal_parameters=test_thermal_parameters)
    temp_response = pulse_run['T']
        #(temp_response.temp_response).apply(lambda x: float(x))   
            #temp_response["temp_response"] = float(temp_response["temp_response"]) 
            #temp_response.to_csv('temp_response/tempresponse' + "_" + str(k) + "_" + str(iso) + '.csv') 
    temp_response["loop"] = str(m) + "_loop_all" 
    list_dfs.append(temp_response)

In [ ]:
pd.concat(list_dfs).to_csv("test_noemms_ssp.csv")

In [ ]:
pd.concat(list_dfs).to_csv("fair_temp_response_futssp_noemms.csv")

In [ ]:
pd.concat(list_dfs).to_csv("fair_temp_response_1980_2020_nousa.csv")

In [ ]:
pd.concat(list_dfs).to_csv("fair_temp_response_1750_2100_test_min11980.csv")

In [ ]:
data = pd.read_csv('long_term_emissions_data.csv')  

In [ ]:
data1 = pd.read_csv("country_lvl_emms.csv")

In [ ]:
data_zwe = data1[data1["ISO3"] == "ZWE"]

In [ ]:
data_zwe = data_zwe[["Year", "Total"]]

In [ ]:
data_zwe.rename(columns = {'Total':'Total_iso'}, inplace = True)

In [ ]:
data_new = pd.merge(data, data_zwe, on = "Year")

In [ ]:
data_new["Total"] = data_new["Total"] - data_new["Total_iso"]

In [ ]:
data_new

In [ ]:
data

In [ ]:
data_new = data

In [ ]:
data_new

In [ ]:
data_new = data_new[["Year", "Total"]]

In [ ]:
data_new.rename(columns = {'Total':'carbon_dioxide'}, inplace = True) #change name to match emissions data

In [ ]:
data_new.rename(columns = {'Year':'year'}, inplace = True) #change name to match emissions data

In [ ]:
data1.rename(columns = {'Year':'year'}, inplace = True) #change name to match emissions data

In [ ]:
data_new["year"] = pd.to_numeric(data_new["year"]) 

In [ ]:
data_new = pd.merge(data_new, data1, on = "year")

In [ ]:
data_new

In [ ]:
data_new["carbon_dioxide"] = data_new["carbon_dioxide"] - data_new["Total"]

In [ ]:
data_new

In [35]:
list_dfs = []
for m in range(1,len(df)): 
  #  for i in master_array[9]:
        # shut off emissions from country i
#        data_iso = data1[data1["ISO3"] == i]
 #       data_iso = data_iso[["Year", "Total"]]
  #      data_iso.rename(columns = {'Total':'Total_iso'}, inplace = True)
   #     data_new = pd.merge(data, data_iso, on = "Year")
    #    data_new["Total"] = data_new["Total"] - data_new["Total_iso"]
    data_new = data
    data_new = data_new[["Year", "Total"]]
    data_new.rename(columns = {'Total':'carbon_dioxide'}, inplace = True) #change name to match emissions data
    data_new.rename(columns = {'Year':'year'}, inplace = True) #change name to match emissions data
    data1.rename(columns = {'Year':'year'}, inplace = True) #change name to match emissions data
    data_new["year"] = pd.to_numeric(data_new["year"]) 
    data_new = pd.merge(data_new, data1, on = "year")
    data_new["carbon_dioxide"] = data_new["carbon_dioxide"] - data_new["Total"]
    # since the carbon emissions are on MtCO2, we need to convert to GtC
    data_new['carbon_dioxide'] = (data_new['carbon_dioxide'] / 1000) / 3.67 
    data_new = data_new[data_new["year"] >= 1990].reset_index() # only keep 1980 and forward
    data_new['year'] = data_new['year'] - (min(data_new['year']) - 1) 
    #feed updated emissions to test_emissions
    test_emissions[("Test", "carbon_dioxide")] = data_new['carbon_dioxide']
        # test_gas_parameters[("default", "carbon_dioxide")][6] = list(df1["taunum"])[0]
        
        # therefore use central estimates for d1-3, q1; and set q2, q3 to return "correct" TCR/ECS values
    df1 = df[df['idnum'] == m] 
    d1 = 0.903
    d2 = list(df1["d2num"])[0]
    d3 = 355
    q1 = 0.180
    rwf = list(df1["rwfnum"])[0]

    TCR = list(df1["tcrnum"])[0]
    ECS = TCR / rwf
    F_2x = 3.759

    v1 = (1-(d1/69.66) * (1-np.exp(-69.66/d1)) )
    v2 = (1-(d2/69.66) * (1-np.exp(-69.66/d2)) )
    v3 = (1-(d3/69.66) * (1-np.exp(-69.66/d3)) )

    q3 = (((TCR/F_2x) - q1*(v1-v2) - (ECS/F_2x)*v2) / (v3-v2))
    q2 = (ECS/F_2x - q1 -  q3)

    test_thermal_parameters["default",2][1] = q2
    test_thermal_parameters["default",3][1] = q3

            #test_thermal_parameters = pd.DataFrame([[d1,d2,d3],[q1,q2,q3]],
             #                                      index=['d','q'],
              #                                     columns=pd.MultiIndex.from_product([['default'],
                      #                                                                 [1,2,3]]))
    pulse_run = run_FaIR(emissions_in=test_emissions,
                         forcing_in=test_forcing,
                         gas_parameters=test_gas_parameters,
                         thermal_parameters=test_thermal_parameters)
    temp_response = pulse_run['T']
        #(temp_response.temp_response).apply(lambda x: float(x))   
            #temp_response["temp_response"] = float(temp_response["temp_response"]) 
            #temp_response.to_csv('temp_response/tempresponse' + "_" + str(k) + "_" + str(iso) + '.csv') 
    temp_response["loop"] = str(m) + "_loop_all" 
    list_dfs.append(temp_response)

Integrating 1 scenarios, 1 gas cycle parameter sets, 1 thermal response parameter sets, over ['carbon_dioxide'] forcing agents, between 0 and 110...


100%|████████████████████████████████| 110/110 [00:00<00:00, 6003.64 timestep/s]

Integrating 1 scenarios, 1 gas cycle parameter sets, 1 thermal response parameter sets, over ['carbon_dioxide'] forcing agents, between 0 and 110...



100%|████████████████████████████████| 110/110 [00:00<00:00, 5609.40 timestep/s]

Integrating 1 scenarios, 1 gas cycle parameter sets, 1 thermal response parameter sets, over ['carbon_dioxide'] forcing agents, between 0 and 110...


...

100%|████████████████████████████████| 110/110 [00:00<00:00, 5767.60 timestep/s]

Integrating 1 scenarios, 1 gas cycle parameter sets, 1 thermal response parameter sets, over ['carbon_dioxide'] forcing agents, between 0 and 110...



100%|████████████████████████████████| 110/110 [00:00<00:00, 5742.90 timestep/s]


Integrating 1 scenarios, 1 gas cycle parameter sets, 1 thermal response parameter sets, over ['carbon_dioxide'] forcing agents, between 0 and 110...


100%|████████████████████████████████| 110/110 [00:00<00:00, 5770.63 timestep/s]


In [125]:
pd.concat(list_dfs).to_csv("fair_temp_resp_k80_hist_fut_bilateralfull.csv")

In [73]:
master_array[1]

array(['LIE', 'LTU', 'LUX', 'MAC', 'MKD', 'MDG', 'MWI', 'MYS', 'MDV',
       'MLI', 'MLT', 'MHL', 'MTQ', 'MRT', 'MUS', 'MYT', 'MEX', 'MNG',
       'MNE', 'MSR', 'MAR', 'MOZ', 'MMR', 'NAM', 'NRU', 'NPL', 'NLD',
       'NCL', 'NZL', 'NIC', 'NER', 'NGA', 'NIU', 'NOR', 'PSE', 'OMN',
       'PAK', 'PLW', 'PAN', 'PNG', 'PRY', 'PER', 'PHL', 'BOL', 'POL',
       'PRT', 'PRI', 'QAT', 'CMR', 'KOR', 'MDA', 'SDN', 'REU', 'ROU',
       'RUS', 'RWA', 'SHN', 'LCA', 'WSM', 'STP', 'SAU', 'SEN', 'SRB',
       'SYC', 'SLE', 'SGP', 'SVK', 'SVN', 'SLB', 'SOM', 'ZAF', 'ESP',
       'LKA', 'KNA', 'SPM', 'VCT', 'SUR', 'SWZ', 'SWE', 'CHE', 'SYR',
       'TWN', 'TJK', 'THA', 'TLS', 'TGO', 'TON', 'TTO', 'TUN', 'TUR',
       'TKM', 'TCA', 'TUV', 'UGA', 'UKR', 'ARE', 'GBR', 'TZA', 'USA',
       'URY', 'UZB', 'VUT', 'VEN', 'VNM', 'WLF', 'YEM', 'ZMB', 'ZWE'],
      dtype=object)